In [ ]:
import numpy as np
import pandas as pd

pd.options.plotting.backend = "plotly"

from gettsim import (
    compute_taxes_and_transfers,
    create_synthetic_data,
    set_up_policy_environment,
)

# Parameteranpassung in GETTSIM - Anhebung des Kindergelds

In der Präsenzphase haben wir gesehen, dass Besserverdiener durch den Kinderfreibetrag einen höheren Steuervorteil haben als Haushalte, die Kindergeld bekommen. Wir wollen in der Selbstlernphase eine Reform untersuchen, nach der der Staat Familien unabhängig vom Einkommen die gleichen Steuervorteile gewährt.

Hierfür gibt es zwei Möglichkeiten:

a) Abschaffung des Freibetrags, sodass alle Haushalte nur Kindergeld beziehen

b) Erhöhung des Kindergelds, sodass die Günstigerprüfung auch für hohe Einkommen zu Gunsten des Kindergelds ausfällt

Eine Senkung des Freibetrags hätte vermutlich vor dem Verfassungsgericht keinen Bestand (für Interessierte am Ende des Notebooks mehr Details), weshalb wir uns die Erhöhung des Kindergelds ansehen. 

Konkret untersuchen wir den Effekt der **Anhebung des Kindergelds** um jährlich **800€**, was den Vorteil des Kinderfreibetrags komplett ausgleichen würde. Der Übersichtlichkeit halber beschränken wir uns auf Familien mit einem Kind, der Vergleich ist nun also nicht mehr zwischen Haushalten mit variierender Anzahl an Kindern, sondern zwischen der Gesamtfinanzsituation der Haushalte mit und ohne einer Kindergeldreform.

Zunächst erstellen wir einen Datensatz, welcher als Grundlage für die folgenden Berechnungen dienen soll.

In [ ]:
min_einkommen = 1500
max_einkommen = 8000
anzahl_schritte = 131


df_2e_1k = create_synthetic_data(
    n_adults=2,
    n_children=1,
    specs_heterogeneous={
        "bruttolohn_m": [
            [i, i, 0]
            for i in np.linspace(min_einkommen, max_einkommen, anzahl_schritte)
        ],
    },
)

df_2e_1k

Für Aufgabe 1 benötigen Sie den jährlichen Bruttolohn auf Haushaltsebene. Versuchen Sie diesen Code genau zu verstehen. Wir haben hier die [transform Methode](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.transform.html) von pandas verwendet. Dadurch wird der Output Vektor auf die Länge des DataFrames "gestreckt". Mit `df_2e_1k.groupby("tu_id")["bruttolohn"].sum()` würde nur ein Wert je Haushalt ausgegeben werden.

In [ ]:
df_2e_1k["bruttolohn"] = df_2e_1k["bruttolohn_m"] * 12
df_2e_1k["bruttolohn_hh"] = df_2e_1k.groupby("tu_id")["bruttolohn"].transform("sum")

## Ausgangsszenario: Steuern / Transfers wie in GETTSIM für 2023 implementiert

Zunächst setzen wir wieder das in GETTSIM implementierte Steuersystem für 2023 auf.

In [ ]:
params_dict, policy_func_dict = set_up_policy_environment(2023)

Anschließend rufen wir GETTSIM auf und berechnen das jährliche Kindergeld auf Steuersubjektebene

In [ ]:
ausgangsszenario = compute_taxes_and_transfers(
    df_2e_1k,
    functions=policy_func_dict,
    params=params_dict,
    targets=[
        "kindergeld_m_tu",
        "eink_st_tu",
        "soli_st_tu",
    ],
)

ausgangsszenario

Und schließlich bereiten wir die Daten etwas auf. Nicht vergessen: Die nachfolgende Zelle können Sie nur einmal ausführen. Wenn Sie sie erneut ausführen möchten, führen Sie vorher nochmal die Zelle direkt oberhalb aus.

In [ ]:
# Wieder die tu_id an das DataFrame joinen
ausgangsszenario = ausgangsszenario.join(df_2e_1k[["tu_id", "bruttolohn_hh"]])
# Jährliches Kindergeld auf Ebene der Steuersubjekte
ausgangsszenario["kindergeld_tu"] = ausgangsszenario["kindergeld_m_tu"] * 12
# Lösche monatliche Werte
ausgangsszenario = ausgangsszenario.drop(["kindergeld_m_tu"], axis=1)
# Behalte nur eine Zeile pro Steuersubjekt
ausgangsszenario = ausgangsszenario.drop_duplicates("tu_id")
# Index setzen
ausgangsszenario = ausgangsszenario.set_index("bruttolohn_hh")
# Ändere Reihenfolge der Spalten
ausgangsszenario = ausgangsszenario[["kindergeld_tu", "eink_st_tu", "soli_st_tu"]]

ausgangsszenario

## Aufgabe 1: Kindergeld im Status quo

Wie viel Kindergeld erhalten Haushalte mit einem Kind mit einem jährlichen Bruttolohn von 39_600€ / 81_600€ / 102_000€ ?

**Tipp** 

`bruttolohn_hh` ist zur Zeit der Index des DataFrames, daher ist es am einfachsten, wenn Sie die `query`-Funktion verwenden.

## GETTSIM Parameter

Um zu verstehen, wie Politikänderungen in GETTSIM implementierbar sind, schauen wir uns ein wenig in `params_dict` um, welches wir oben durch das Aufrufen der `set_up_policy_environment` Funktion erstellt haben. Bitte vollziehen Sie dies Schritt für Schritt nach! 

NB: Das gesamte `params_dict` könnte man sich durch Eingabe von `params_dict` anzeigen lassen. Das ist aufgrund seiner schieren Größe jedoch einigermaßen unlesbar. Die folgende Syntax brauchen Sie nicht zu verstehen. Einziger Zweck ist, die `keys` des `dict` ordentlich darzustellen.

In [ ]:
print(*params_dict.keys(), sep="\n")

Wir wollen das Kindergeld ändern, also schauen wir bei `kindergeld` weiter.

In [ ]:
print(*params_dict["kindergeld"].keys(), sep="\n")

Und noch einmal:

In [ ]:
params_dict["kindergeld"]["kindergeld"]

## Aufgabe 2: Parameter des Kindergeldes

Finden Sie heraus, was die einzelnen Parameter von `params_dict["kindergeld"]["kindergeld"]` zu bedeuten haben.

**Tipp:**
Für das Jahr 2022 ergeben sich folgende Parameter:

In [ ]:
params_dict2022, policy_func_dict2022 = set_up_policy_environment(2022)
params_dict2022["kindergeld"]["kindergeld"]

## Neues Steuer-/Transfersystem mit modifizierten Parametern

Jetzt implementieren wir die Kindergelderhöhung.

Zunächst brauchen wir eine sogenannte `deepcopy` des `param_dict`. Sie brauchen nicht nachzuvollziehen,
was diese macht. Lediglich das Ergebnis ist wichtig: Eine exakte Kopie der Parameter des 2023er 
Steuersystems aus GETTSIM.

In [ ]:
from copy import deepcopy

params_dict_reformiert = deepcopy(params_dict)

Um die o.g. Kindergelderhöhung im Kontext unseres Beispiels zu berechnen, passen wir die Parameter entsprechend an.

## Aufgabe 3: Anpassung der Reformparameter

Wie im Notebook von letzter Woche zu sehen muss das Kindergeld jährlich um etwa 800€ erhöht werden, um den Steuervorteil für Besserverdiener auszugleichen. Die Parameter in `params_dict_reform` sind auf monatlicher Basis gegeben. Passen Sie sie entsprechend unserer Reform an. 

Nun rufen wir GETTSIM auf. Als Rückgabe benötigen wir die Identifizierungsnummer für das
Steuersubjekt, das Kindergeld, sowie Einkommensteuer und Solidaritätszuschlag.

Bitte vergegenwärtigen Sie sich die Struktur:

* In der letzten Präsenzphase haben wir verschiedene Haushaltstypen verglichen
* Nun vergleichen wir dieselben Haushaltstypen über verschiedene Szenarien hinweg

## Aufgabe 4: Reformszenario in GETTSIM
Passen Sie die folgende Zelle entsprechend an, indem Sie die nötigen Parameter/Variablen anpassen. Bis auf die erste Zeile ist sie von oben kopiert. Sie müssen also die Variablen/Parameter von letzter Woche durch die dieser Woche anpassen.

In [ ]:
reformszenario = compute_taxes_and_transfers(
    df_2e_1k,
    functions=policy_func_dict,
    params=params_dict_reformiert,
    targets=[
        "kindergeld_m_tu",
        "eink_st_tu",
        "soli_st_tu",
    ],
)

In [ ]:
# Wieder die tu_id an das DataFrame joinen
reformszenario = reformszenario.join(df_2e_1k[["tu_id", "bruttolohn_hh"]])
# Jährliches Kindergeld auf Ebene der Steuersubjekte
reformszenario["kindergeld_tu"] = reformszenario["kindergeld_m_tu"] * 12
# Lösche monatliche Werte
reformszenario = reformszenario.drop(["kindergeld_m_tu"], axis=1)
# Behalte nur eine Zeile pro Steuersubjekt
reformszenario = reformszenario.drop_duplicates("tu_id")
# Index setzen
reformszenario = reformszenario.set_index("bruttolohn_hh")
# Ändere Reihenfolge der Spalten
reformszenario = reformszenario[["kindergeld_tu", "eink_st_tu", "soli_st_tu"]]

reformszenario

### Zusammenfügen der beiden DataFrames

In [ ]:
vergleich = pd.concat(
    [ausgangsszenario, reformszenario],
    keys=["vor Reform", "nach Reform"],
    names=["Szenario", "bruttolohn_hh"],
)

vergleich

## Aufgabe 5: Berechnung des Vorteils

Wir bestimmen im folgenden die Differenz der Einkommensteuer und Kindergeldeinnahmen des Haushalts.

In [ ]:
differenz_einkommensteuer = (
    vergleich.loc["nach Reform", "eink_st_tu"]
    - vergleich.loc["vor Reform", "eink_st_tu"]
).to_frame("Differenz Einkommensteuer")

In [ ]:
differenz_kindergeld = (
    vergleich.loc["nach Reform", "kindergeld_tu"]
    - vergleich.loc["vor Reform", "kindergeld_tu"]
).to_frame("Differenz Kindergeld")

Berechnen Sie nun den Steuervorteil, der sich aus der Reform ergibt. Konzeptionell orientiert sich dies an der Berechnung des Steuervorteils in der letzten Präsenzphase.

## Aufgabe 6: Differenz im Kindergeld 

Plotten Sie die Differenz der Kindergeldzahlung vor und nach der Reform.

Plotten Sie die Differenz der Einkommensteuerzahlung durch die Reform.

Plotten Sie den durch die Reform entstandenen Steuervorteil.

## Aufgabe 7: Interpretieren Sie die Graphen

*Ihre Antwort hier*

## Aufgabe 8: Gesamter Steuervorteil


Wiederholen Sie die Berechnung des Steuervorteils von oben, beziehen Sie nun jedoch den Soli mit ein.

Erstellen Sie zwei Grafiken, wieder auf Ebene der Steuersubjekte: 

1. Solidaritätszuschlag nach Gesamteinkünften
2. Gesamter Steuervorteil nach Gesamteinkünften

Für die Berechnung des Steuervorteils können Sie auf dem Code von oben aufbauen.


Sie sollten keine Unterschiede zwischen den Graphen sehen. [Wikipedia](https://de.wikipedia.org/wiki/Kinderfreibetrag) schreibt zur Interaktion zwischen Soli und Kinderfreibetrag: "Solidaritätszuschlag und Kirchensteuer werden stets unter Berücksichtigung des Kinderfreibetrags berechnet."

Wieso sehen Sie also keine Unterschiede?

*Ihre Antwort*

## Aufgabe 9: Ausblick

Schauen Sie erneut auf den Reformvorschlag. Warum funktioniert die Art der Modellierung (d.h., das 
Verändern der Parameter für das Kindergeld) solange wir Leistungen der Grundsicherung (Bürgergeld,
Sozialhilfe) nicht betrachten? Warum funktioniert dieser Ansatz nicht mehr, sobald wir diese auch modellieren?

*Ihre Antwort*


# Anhang: Die relevantesten Urteile des Bundesverfassungsgerichts zum Kinderfreibetrag


## Historischer Überblick:

1960er bis 1974: "Duales System": Kindergeld mit Einkommensgrenze + einkommensunabhängiger Anspruch auf Kinderfreibetrag

1974: Einkommensunabhängiges Kindergeld, kein Kinderfreibetrag

1976: Urteil des Bundesverfassungsgerichts: Existenzminimum auch für hohe Einkommen steuerfrei stellen ist nicht notwendig

1983: Rückkehr zum "dualen System": Kindergeld sinkt im Einkommen + einkommensunabhängiger Anspruch auf (niedrigen) Kinderfreibetrag 

1990: Verfassungsgericht erklärt Kürzung des Kindergelds für Besserverdienende für grundgesetzwidrig, solange Kindergeld + Kinderfreibetrag nicht auch für Besserverdiende das Existenzminimum steuerfrei stellt --> deutliche Anhebung des Kinderfreibetrags

1998: Bestätigung des Urteils von 1990

seit 2004: Günstigerprüfung Kindergeld/ Kinderfreibetrag


## Berücksichtigte Grundgesetzartikel:

Art 1 Abs 1 GG: *Die Würde des Menschen ist unantastbar. Sie zu achten und zu schützen ist Verpflichtung aller staatlichen Gewalt.*

Art. 3 Abs. 1 GG: *Alle Menschen sind vor dem Gesetz gleich.*

Art. 6 Abs. 1 GG: *Ehe und Familie stehen unter dem besonderen Schutze der staatlichen Ordnung.*

Art 20 Abs. 1 GG: *Die Bundesrepublik Deutschland ist ein demokratischer und sozialer Bundesstaat.*


## Urteile des Bundesverfassungsgericht

Es ist nicht notwendig, das Existenzminimum auch für hohe Einkommen steuerfrei zu stellen - [BVerfGE 43, 108: Beschluss vom 23. November 1976](https://www.servat.unibe.ch/tools/DfrInfo?Command=ShowPrintText&Name=bv043108): 

1. "Die wirtschaftliche Belastung der Eltern durch Unterhaltsverpflichtungen gegenüber ihren Kindern gehört zu den die Leistungsfähigkeit beeinträchtigenden Umständen, die im Einkommenssteuerrecht nicht außer acht bleiben dürfen, sofern nicht ein anderweitiger Ausgleich gewährt wird."

2. "**Der Gesetzgeber ist jedoch nicht verpflichtet, die nach der sozialen Stellung verschiedenen Aufwendungen für den Unterhalt der Kinder in vollem Umfang als steuerliche Entlastung zu berücksichtigen.** Insbesondere kann er den Familienlastenausgleich so gestalten, daß die an sich schon bestehende Ungleichheit der Startchancen von Kindern mit verschiedenen Einkommensverhältnissen der Eltern nicht noch verstärkt wird."


Rücknahme des Urteils von 1976 - [BVerfGE 82, 60: Beschluss vom 29. Mai 1990](https://www.servat.unibe.ch/tools/DfrInfo?Command=ShowPrintText&Name=bv082060): 

"Bei der Einkommensbesteuerung muß ein Betrag in Höhe des Existenzminimums der Familie steuerfrei bleiben; nur das darüber hinausgehende Einkommen darf der Besteuerung unterworfen werden"

Auszug aus der Begründung:

Argument 1: 
 "Ausgangspunkt der verfassungsrechtlichen Beurteilung ist der Grundsatz, daß der Staat dem Steuerpflichtigen sein Einkommen insoweit steuerfrei belassen muß, als es zur Schaffung der Mindestvoraussetzungen für ein menschenwürdiges Dasein benötigt wird. Dieses verfassungsrechtliche Gebot folgt aus Art. 1 Abs. 1 GG in Verbindung mit dem Sozialstaatsgrundsatz des Art. 20 Abs. 1 GG. **Ebenso wie der Staat nach diesen Verfassungsnormen verpflichtet ist, dem mittellosen Bürger diese Mindestvoraussetzungen erforderlichenfalls durch Sozialleistungen zu sichern, darf er dem Bürger das selbst erzielte Einkommen bis zu diesem,Betrag - der im, folgenden als Existenzminimum bezeichnet wird - nicht entziehen.** Aus den genannten Verfassungsnormen, zusätzlich aber auch aus Art. 6 Abs. 1 GG, folgt ferner, daß bei der Besteuerung einer Familie das Existenzminimum sämtlicher Familienmitglieder steuerfrei bleiben muß."

Argument 2:
"Prüfungsmaßstab ist insoweit Art. 3 Abs. 1 GG, wobei die in Art. 6 Abs. 1 GG enthaltene Grundsatzentscheidung für den Schutz der Familie mit zu beachten ist.
Der allgemeine Gleichheitssatz ist verletzt, wenn der Staat eine Gruppe von Normadressaten im Vergleich zu anderen Normadressaten anders behandelt, obwohl zwischen beiden Gruppen keine Unterschiede von solcher Art und solchem Gewicht bestehen, daß sie die ungleiche Behandlung rechtfertigen könnten. Daraus folgt für das Gebiet des Steuerrechts, daß die Besteuerung an der wirtschaftlichen Leistungsfähigkeit ausgerichtet werden muß. Das gilt insbesondere im Einkommensteuerrecht, das auf die Leistungsfähigkeit des einzelnen Steuerpflichtigen hin angelegt ist. **Die für den Steuerpflichtigen unvermeidbare Sonderbelastung durch Unterhaltsverpflichtungen mindert seine Leistungsfähigkeit und darf ohne Verstoß gegen Art. 3 Abs. 1 GG vom Gesetzgeber nicht unberücksichtigt bleiben**.""

Argument 3:
"Der Höhe nach muß der Staat bei der Beurteilung der steuerlichen Leistungsfähigkeit den Unterhaltsaufwand für Kinder des Steuerpflichtigen in dem Umfang als besteuerbares Einkommen außer Betracht lassen, in dem die Unterhaltsaufwendungen zur Gewährleistung des Existenzminimums der Kinder erforderlich sind. "
"Das folgt mittelbar aus den Erwägungen, die es gebieten, das Existenzminimum der Familie steuerfrei zu lassen. **Soweit das Einkommen der Familie benötigt wird, um ihr die Mindestvoraussetzungen für ein menschenwürdiges Dasein zu gewährleisten, ist es - unabhängig vom sozialen Status der Familie - nicht disponibel und kann nicht Grundlage der steuerlichen Leistungsfähigkeit sein.** Wird die Besteuerung für Kinderlose und Steuerpflichtige mit Kindern nach einem einheitlichen Tarif vorgenommen, so werden die letzteren gegenüber den ersteren benachteiligt, wenn von ihrem Einkommen der Unterhaltsaufwand für Kinder nicht wenigstens in Höhe des Existenzminimums abgezogen wird; denn sie werden dadurch im Ergebnis einer höheren Steuerbelastung unterworfen als kinderlose Ehepaare oder Alleinstehende, weil sie bei gleichem Ausgangseinkommen die gleiche Steuerlast tragen wie Kinderlose, obwohl ihr Einkommen in Höhe des Existenzminimums der Kinder gebunden ist und ihnen daher insoweit nicht zur freien Verwendung zur Verfügung steht. "


Bestätigung des Urteils von 1990 - [BVerfGE 42, 93: Beschluss vom 10. November 1998](https://www.servat.unibe.ch/tools/DfrInfo?Command=ShowPrintText&Name=bv082060):

"Art. 6 Abs. 1 GG gebietet, bei der Besteuerung einer Familie das Existenzminimum sämtlicher Familienmitglieder steuerfrei zu belassen: Dabei bildet das sozialhilferechtlich definierte Existenzminimum die Grenze für das einkommensteuerliche Existenzminimum, die über-, aber nicht unterschritten werden darf. Das einkommensteuerliche Existenzminimum ist für alle Steuerpflichtigen - unabhängig von ihrem individuellen Grenzsteuersatz - in voller Höhe von der Einkommensteuer freizustellen. "